[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/pukulenam/abstractive_sum/blob/main/ML_model/Seq2seq_Model.ipynb)

## Import Library

In [ ]:
!pip install datasets
from datasets import load_dataset

dataset = load_dataset("csebuetnlp/xlsum",'indonesian')

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 346 kB 25.3 MB/s 
     |████████████████████████████████| 212 kB 54.3 MB/s 
     |████████████████████████████████| 1.1 MB 60.5 MB/s 
     |████████████████████████████████| 86 kB 500 kB/s 
     |████████████████████████████████| 86 kB 7.1 MB/s 
     |████████████████████████████████| 140 kB 5.1 MB/s 
     |████████████████████████████████| 596 kB 57.2 MB/s 
     |████████████████████████████████| 127 kB 73.4 MB/s 
     |████████████████████████████████| 144 kB 62.0 MB/s 
     |████████████████████████████████| 94 kB 4.5 MB/s 
     |████████████████████████████████| 271 kB 65.4 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
     

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Dataset xlsum downloaded and prepared to /root/.cache/huggingface/datasets/csebuetnlp___xlsum/indonesian/2.0.0/518ab0af76048660bcc2240ca6e8692a977c80e384ffb18fdddebaca6daebdce. Subsequent calls will reuse this data.


  0%|          | 0/3 [00:00<?, ?it/s]

In [ ]:
import tensorflow as tf
from tensorflow.keras import callbacks, models, layers, preprocessing as kprocessing #(2.6.0)
import pandas as pd
import json

In [ ]:
from nltk.corpus import stopwords
import regex as re

import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

## Splitting Datasets

In [ ]:
dataset['train']['summary'][0]
print(len(dataset['train']))

38242


In [ ]:
x_text = dataset['train']['text'][1001:11001]
x_sum = dataset['train']['summary'][1001:11001]
y_text = dataset['test']['text'][1001:11001]
y_sum = dataset['test']['summary'][1001:11001]

## Data Preprocessing

### Text Cleaning

In [ ]:
i = 0
for text in x_text:
  text = text.lower()
  x_text[i] = re.sub("!\"#\$%&\(\)\*\+,-\.\/:;<=>\?@\[\]\^_`{\|}~", "", text)
  i+=1
j = 0
for text in x_sum:
  text = text.lower()
  x_sum[j] = re.sub("!\"#\$%&\(\)\*\+,-\.\/:;<=>\?@\[\]\^_`{\|}~", "", text)
  j+=1

In [ ]:
i = 0
for text in y_text:
  text = text.lower()
  y_text[i] = re.sub("!\"#\$%&\(\)\*\+,-\.\/:;<=>\?@\[\]\^_`{\|}~", "", text)
  i+=1
j = 0
for text in y_sum:
  text = text.lower()
  y_sum[j] = re.sub("!\"#\$%&\(\)\*\+,-\.\/:;<=>\?@\[\]\^_`{\|}~", "", text)
  j+=1

### Removing Stopwords

In [ ]:
stopword = stopwords.words("indonesian")

In [ ]:
i = 0
for text in x_text:
  temp=""
  text=text.split(" ")
  for word in text:
    if word not in stopword:
      temp = temp+" "+word
  x_text[i] = temp
  i+=1

j = 0
for text in x_sum:
  temp=""
  text=text.split(" ")
  for word in text:
    if word not in stopword:
      temp = temp+" "+word
  x_sum[j] = temp
  j+=1

In [ ]:
i = 0
for text in y_text:
  temp=""
  text=text.split(" ")
  for word in text:
    if word not in stopword:
      temp = temp+" "+word
  y_text[i] = temp
  i+=1

j = 0
for text in y_sum:
  temp=""
  text=text.split(" ")
  for word in text:
    if word not in stopword:
      temp = temp+" "+word
  y_sum[j] = temp
  j+=1

### Converting to Dataframes

In [ ]:
dtf_X = pd.DataFrame(x_text)
dtf_y = pd.DataFrame(x_sum)

In [ ]:
dtf = pd.concat([dtf_X, dtf_y], axis=1)

In [ ]:
dtf.columns = ["x_text", "x_sum"]
i = 100
dtf_train = dtf.iloc[i+1:]
dtf_test = dtf.iloc[:i+1]
dtf_test

x_text  \
0     justin bieber merayakan ulang 19 klub london....   
1     megawati mengangkat anaknya ketua kepengurusa...   
2     pengamat neng dara affiah, dosen sosiologi un...   
3     ponsel blackberry bersaing iphone android per...   
4     arsene wenger kepercayaan pemain arsenal ting...   
..                                                 ...   
96    podcast bertajuk janda becanda, tania mengund...   
97    merenungkan periode hidup itu, salah sekian k...   
98    coretan dianggap karya beethoven dikenal guba...   
99    kerja, kantor sibuk penuh tekanan, ruang medi...   
100   robot ai diajari mengakses memori manfaat sek...   

                                                 x_sum  
0     perayaan ulang justin bieber london dilaporka...  
1     perita penangkapan kader pdip kpk, megawati m...  
2     produk bersertifikat halal marak, makanan, ku...  
3     keuntungan produsen blackberry research in mo...  
4     manajer arsenal, arsene wenger, timnya menang...  
..                                                 ...  
96    intania fajar, ditinggal meninggal suami berc...  
97    bayangkan berusia 12 tahun, keluarga pindah k...  
98    gubahan beethoven himne kuno berhasil ditemuk...  
99    membaca penelitian terbaru meditasi? belum, m...  
100   bersama, berdampingan robot cepat dibandingka...  

[101 rows x 2 columns]

### Tokenizing

In [ ]:
## tokenize text
num_word = 10000
tokenizer = kprocessing.text.Tokenizer(num_words=num_word, lower=True, split=' ', oov_token=None)
tokenizer.fit_on_texts(dtf_train["x_text"])
art_vocabulary = {0:"<PAD>"}
art_vocabulary.update(tokenizer.index_word)
print(len(art_vocabulary), "words")
## create sequence
art_text2seq = tokenizer.texts_to_sequences(dtf_train["x_text"])
## padding sequence
X_train = kprocessing.sequence.pad_sequences(art_text2seq, 
                                             maxlen=500, padding='post', truncating="post")
print(X_train.shape[0], "sequences of length", X_train.shape[1])

115420 words
9899 sequences of length 500


In [ ]:
## tokenize text
tokenizer.fit_on_texts(dtf_test["x_text"])
art_vocabulary.update(tokenizer.index_word)
print(len(art_vocabulary), "words")
## create sequence
art_text2seq = tokenizer.texts_to_sequences(dtf_test["x_text"])
## padding sequence
X_test = kprocessing.sequence.pad_sequences(art_text2seq, 
                                             maxlen=X_train.shape[1], padding='post', truncating="post")
print(X_test.shape[0], "sequences of length", X_test.shape[1])

116396 words
101 sequences of length 500


In [ ]:
# Add START and END tokens to the summaries (y)
special_tokens = ("xstartx", "xendx")
dtf_train["x_sum"] = dtf_train["x_sum"].apply(lambda x: 
                     special_tokens[0]+' '+x+' '+special_tokens[1])
dtf_test["x_sum"] = dtf_test["x_sum"].apply(lambda x: 
                     special_tokens[0]+' '+x+' '+special_tokens[1])
dtf_test["x_sum"][i]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """


'xstartx  bersama, berdampingan robot cepat dibandingkan pikirkan. memahami mereka. xendx'

In [ ]:
## tokenize text
tokenizer.fit_on_texts(dtf_train["x_sum"])
sum_vocabulary = {0:"<PAD>"}
sum_vocabulary.update(tokenizer.index_word)
print(len(sum_vocabulary), "words")
## create sequence
sum_text2seq = tokenizer.texts_to_sequences(dtf_train["x_sum"])
## padding sequence
y_train = kprocessing.sequence.pad_sequences(sum_text2seq,
                                             maxlen=15, padding="post", truncating="post")
print(y_train.shape[0], "sequences of length", y_train.shape[1])

117636 words
9899 sequences of length 15


In [ ]:
## tokenize text
tokenizer.fit_on_texts(dtf_test["x_sum"])
sum_vocabulary.update(tokenizer.index_word)
print(len(sum_vocabulary), "words")
## create sequence
sum_text2seq = tokenizer.texts_to_sequences(dtf_test["x_sum"])
## padding sequence
y_test = kprocessing.sequence.pad_sequences(sum_text2seq,
                                             maxlen=y_train.shape[1], padding="post", truncating="post")
print(y_test.shape[0], "sequences of length", y_test.shape[1])

117655 words
101 sequences of length 15


### Embedding

In [ ]:
#!pip install gensim
import gensim.downloader
nlp = gensim.downloader.load("glove-wiki-gigaword-300")

[==================================================] 100.0% 376.1/376.1MB downloaded


In [ ]:
## start the matrix (length of vocabulary x vector size) with all 0s
import numpy as np
art_embeddings = np.zeros((len(art_vocabulary)+1, nlp.vector_size), dtype='float32')
for word,idx in art_vocabulary.items():
  ## update the row with vector
  try:
    art_embeddings[idx] = nlp[word]
  except:
  ## if word not in model then skip and the row stays all 0s
    pass

In [ ]:
## start the matrix (length of vocabulary x vector size) with all 0s
import numpy as np
sum_embeddings = np.zeros((len(sum_vocabulary)+1, nlp.vector_size), dtype='float32')
for word,idx in sum_vocabulary.items():
  ## update the row with vector
  try:
    sum_embeddings[idx] = nlp[word]
  except:
  ## if word not in model then skip and the row stays all 0s
    pass

## Building the Model

### Training Model

In [ ]:
art_embeddings.shape[0]-1

In [ ]:
# Encoder
lstm_units = 400
embeddings_size=300
x_inp=layers.Input(name="x_inp", shape=(X_train.shape[1],))
layer_xEmb = layers.Embedding(name="xEmb", input_dim=art_embeddings.shape[0], output_dim=art_embeddings.shape[1], 
                              weights = [art_embeddings], trainable=True)
x_emb = layer_xEmb(x_inp) 
art_bidirectional_lstm = layers.Bidirectional(layers.LSTM(units=lstm_units, 
                 dropout=0.4, return_sequences=True, 
                 return_state=True), name="x_lstm_1")
x_out,forward_h, forward_c, backward_h, backward_c = art_bidirectional_lstm(x_emb)
state_h = layers.Concatenate()([forward_h, backward_h])
state_c = layers.Concatenate()([forward_c, backward_c])

# Decoder
y_inp = layers.Input(name="y_inp", shape=(None,))
layer_y_emb = layers.Embedding(name="y_emb", input_dim=sum_embeddings.shape[0], output_dim=sum_embeddings.shape[1], 
                               weights = [sum_embeddings], trainable=True)
y_emb = layer_y_emb(y_inp)
sum_lstm = layers.LSTM(name="sum_lstm", units=lstm_units*2, dropout=0.4, return_sequences=True, return_state=True, activation="tanh")
y_out, _, _ = sum_lstm(y_emb, initial_state=[state_h, state_c])

# Dense Layer
dense_layer = layers.TimeDistributed(name="dense", 
              layer=layers.Dense(units=len(sum_vocabulary), 
               activation='softmax'))
y_out = dense_layer(y_out)

In [ ]:
# Compile Model
model = models.Model(inputs=[x_inp, y_inp], outputs=y_out, 
                            name="Seq2Seq")
model.compile(optimizer='adam', loss="sparse_categorical_crossentropy", metrics=['accuracy'])
model.summary()

Model: "Seq2Seq"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 x_inp (InputLayer)             [(None, 500)]        0           []                               
                                                                                                  
 xEmb (Embedding)               (None, 500, 300)     34919100    ['x_inp[0][0]']                  
                                                                                                  
 y_inp (InputLayer)             [(None, None)]       0           []                               
                                                                                                  
 x_lstm_1 (Bidirectional)       [(None, 500, 800),   2243200     ['xEmb[0][0]']                   
                                 (None, 400),                                               

In [ ]:
training = model.fit(x=[X_train, y_train[:,:-1]], 
                     y=y_train.reshape(y_train.shape[0], 
                                       y_train.shape[1], 
                                       1)[:,1:],
                     batch_size=64, 
                     epochs=50, 
                     shuffle=True, 
                     verbose=1, 
                     validation_split=0.3,
                     
                      )

Epoch 1/50
109/109 [==============================] - 79s 655ms/step - loss: 8.4249 - accuracy: 0.0927 - val_loss: 7.2847 - val_accuracy: 0.0976
Epoch 2/50
109/109 [==============================] - 71s 649ms/step - loss: 7.1988 - accuracy: 0.1232 - val_loss: 7.0344 - val_accuracy: 0.1399
Epoch 3/50
109/109 [==============================] - 71s 652ms/step - loss: 7.0180 - accuracy: 0.1294 - val_loss: 6.9543 - val_accuracy: 0.1424
Epoch 4/50
109/109 [==============================] - 72s 657ms/step - loss: 6.8737 - accuracy: 0.1322 - val_loss: 6.8764 - val_accuracy: 0.1462
Epoch 5/50
109/109 [==============================] - 72s 660ms/step - loss: 6.7082 - accuracy: 0.1371 - val_loss: 6.7658 - val_accuracy: 0.1518
Epoch 6/50
109/109 [==============================] - 72s 660ms/step - loss: 6.5327 - accuracy: 0.1441 - val_loss: 6.6669 - val_accuracy: 0.1587
Epoch 7/50
109/109 [==============================] - 72s 661ms/step - loss: 6.3136 - accuracy: 0.1543 - val_loss: 6.5655 - val_ac

### Encoder Model

In [ ]:
# Prediction Encoder
encoder_model = models.Model(inputs=x_inp, outputs=[x_out, state_h, state_c], name="Prediction_Encoder")
encoder_model.summary()

Model: "Prediction_Encoder"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 x_inp (InputLayer)             [(None, 500)]        0           []                               
                                                                                                  
 xEmb (Embedding)               (None, 500, 300)     34919100    ['x_inp[0][0]']                  
                                                                                                  
 x_lstm_1 (Bidirectional)       [(None, 500, 800),   2243200     ['xEmb[0][0]']                   
                                 (None, 400),                                                     
                                 (None, 400),                                                     
                                 (None, 400),                                    

### Decoder Model

In [ ]:
# Prediction Decoder
## double the lstm units if you used bidirectional lstm
lstm_units = lstm_units *2 if any("Bidirectional" in str(layer) for layer in model.layers) else lstm_units
## states of the previous time step
encoder_out = layers.Input(shape=(X_train.shape[1], lstm_units))
state_h, state_c = layers.Input(shape=(lstm_units,)), layers.Input(shape=(lstm_units,))
## decoder embeddings
y_emb2 = layer_y_emb(y_inp)
# y_emb_expand = tf.expand_dims(y_emb2, axis=1)
## lstm to predict the next word
y_out2, state_h2, state_c2 = sum_lstm(y_emb2, initial_state=[state_h, state_c])
## softmax to generate probability distribution over the vocabulary
probs = dense_layer(y_out2)
## compile
decoder_model = models.Model(inputs=[y_inp, encoder_out, state_h, state_c], outputs=[probs, state_h2, state_c2], name="Prediction_Decoder")
decoder_model.summary()

Model: "Prediction_Decoder"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 y_inp (InputLayer)             [(None, None)]       0           []                               
                                                                                                  
 y_emb (Embedding)              (None, None, 300)    35296800    ['y_inp[0][0]']                  
                                                                                                  
 input_2 (InputLayer)           [(None, 800)]        0           []                               
                                                                                                  
 input_3 (InputLayer)           [(None, 800)]        0           []                               
                                                                                 

## Prediction Testing

In [ ]:
dtf_Full = pd.DataFrame(dataset["train"])
dtf_Full

id  \
0                          media-49647079   
1                      indonesia-43826943   
2           160404_dunia_israel_palestina   
3        160819_majalah_australia_sedekah   
4                      indonesia-43459438   
...                                   ...   
38237                121017_gillard_debat   
38238                    majalah-39329999   
38239            130619_seni_teater_gelap   
38240  140708_google_hangouts_discussions   
38241                    majalah-37793159   

                                                     url  \
0           https://www.bbc.com/indonesia/media-49647079   
1       https://www.bbc.com/indonesia/indonesia-43826943   
2      https://www.bbc.com/indonesia/dunia/2016/04/16...   
3      https://www.bbc.com/indonesia/majalah/2016/08/...   
4       https://www.bbc.com/indonesia/indonesia-43459438   
...                                                  ...   
38237  https://www.bbc.com/indonesia/majalah/2012/10/...   
38238     https://www.bbc.com/indonesia/majalah-39329999   
38239  https://www.bbc.com/indonesia/majalah/2013/06/...   
38240  https://www.bbc.com/indonesia/forum/2014/07/14...   
38241     https://www.bbc.com/indonesia/majalah-37793159   

                                                   title  \
0      Gajah mengamuk saat upacara keagamaan, 17 oran...   
1      Apa alasan pemerintah pangkas 14 dalam daftar ...   
2      Rumah warga Palestina pembunuh polisi Israel d...   
3      Beri uang pada pengemis, PM Australia picu per...   
4      Dua anak Soeharto di panggung politik, indikas...   
...                                                  ...   
38237        Komentar GIllard memicu perubahan arti kata   
38238    Negara mana yang penduduknya paling berbahagia?   
38239                       Menonton teater di kegelapan   
38240             Apa tantangan presiden terpilih nanti?   
38241  Penipuan seks lewat Skype, pemerasan dengan me...   

                                                 summary  \
0      Seekor gajah mendadak mengamuk saat prosesi ta...   
1      Presiden Jokowi memutuskan untuk menghapus 14 ...   
2      Pihak keamanan Israel menghancurkan rumah tiga...   
3      Ada istilah 'tidak ada perbuatan baik yang tid...   
4      Diusulkannya Titiek Soeharto -putri mantan pre...   
...                                                  ...   
38237                                           misogyny   
38238     Negara apa yang penduduknya paling berbahagia?   
38239  Teater ini bukan untuk mereka yang suka lampu ...   
38240                                                      
38241       PERINGATAN: Video ini berisi konten seksual.   

                                                    text  
0      Dilaporkan dua orang terluka cukup serius, sem...  
1      Proyek MRT Sudirman- Lebak Bulus tengah dikerj...  
2      Israel secara berkala menghancurkan rumah kelu...  
3      Sebagian memandang Turnbull pelit. Dia adalah ...  
4      Tommy Soeharto dan Titiek Soeharto merupakan k...  
...                                                  ...  
38237  Julia Gillard merupakan perdana menteri peremp...  
38238  Norwegia menjadi negara urutan pertama untuk u...  
38239  Sebuah drama yang dipentaskan di kegelapan tot...  
38240  BBC Indonesia mengadakan diskusi melalui Googl...  
38241  Dalam beberapa bulan terakhir, BBC menyelidiki...  

[38242 rows x 5 columns]

In [ ]:
asd = dtf_Full.at[69,"text"]
dtf_Full.at[69, "text"]

'Yasuo Takamatsu berlatih untuk izin menyelamnya pada Maret 2014 (Foto: Getty Images) Seorang mencari istrinya, seorang lain mencari anak perempuannya yang menjadi korban tsunami yang meluluhlantakkan Jepang empat tahun lalu. Kedua pria itu tahu keluarga mereka pasti tak selamat, tapi mereka tetap menyelam sambil berharap menemukan sesuatu - sekecil apapun. Di bawah perairan Teluk Onagawa, Prefektur Miyagi, di timur laut Jepang, ada kulkas-kulkas, televisi, mobil, truk, sampai peralatan memancing tersebar di dasar laut, di bawah lapisan lumpur. "Bayangkan satu kota besar, ditaruh di mesin penghancur, dan buang semuanya ke dasar lautan," kata seorang oseanografer menggambarkan efek tsunami Jepang. Bumper mobil terlihat di laut dengan kedalaman 546 meter © JAMSTEC/TEAMS Di bawah laut, semuanya terlihat sama seperti saat kedatangan gelombang tsunami. Di permukaan, keadaan telah berubah. Kapal nelayan mulai mencari ikan - makanan pokok Jepang sekaligus juga bagian penting ekonomi warga set

In [ ]:
asd = re.sub("[-()\"#/@;:<>{}`+=~|.!?,]", "", asd)

temp=""
text=asd.split(" ")
for word in text:
  if word not in stopword:
    temp = temp+" "+word
asd = temp
list_asd = []
list_asd.append(asd.strip())
print(list_asd)

["Yasuo Takamatsu berlatih izin menyelamnya Maret 2014 Foto Getty Images Seorang mencari istrinya mencari anak perempuannya korban tsunami meluluhlantakkan Jepang Kedua pria keluarga selamat menyelam berharap menemukan  apapun Di perairan Teluk Onagawa Prefektur Miyagi timur laut Jepang kulkaskulkas televisi mobil truk peralatan memancing tersebar dasar laut lapisan lumpur Bayangkan kota ditaruh mesin penghancur buang dasar lautan oseanografer menggambarkan efek tsunami Jepang Bumper mobil laut kedalaman 546 meter © JAMSTECTEAMS Di laut kedatangan gelombang tsunami Di permukaan berubah Kapal nelayan mencari ikan  makanan pokok Jepang ekonomi warga Sisasisa pelabuhan hancur dibersihkan Kini area beton luas kosong kecuali pojokan berdoa sederhana terbuat halamanhalaman kertas A4 dilapisi plastik bunga krisan plastik berwarna pink pohon natal Tempat pemujaan pegawai Bank 77 Onagawa © Hiromi Tanoue Di berdiri kantor cabang Onagawa Bank Shichijushichi 77 pemujaan mengenangnya Saat alarm per

In [ ]:
tokenizer.fit_on_texts(list_asd)
art_text2seq = tokenizer.texts_to_sequences(list_asd)
## padding sequence
x = kprocessing.sequence.pad_sequences(art_text2seq, 
                                             maxlen=X_train.shape[1], padding='post', truncating="post")
print(tokenizer.index_word)
print(art_text2seq)
print(x.shape)
print(x.shape[0], "sequences of length", x.shape[1])
print(X_test.shape)

{1: 'orang', 2: 'itu', 3: 'indonesia', 4: 'negara', 5: 'ini', 6: 'anak', 7: 'pemerintah', 8: 'xstartx', 9: 'xendx', 10: 'rumah', 11: 'kota', 12: 'presiden', 13: 'saya', 14: 'perempuan', 15: 'dunia', 16: 'warga', 17: 'salah', 18: 'memiliki', 19: 'inggris', 20: 'lalu', 21: 'mereka', 22: 'bbc', 23: 'kelompok', 24: 'masyarakat', 25: 'tersebut', 26: 'kali', 27: 'as', 28: 'tahun', 29: 'polisi', 30: 'terkait', 31: '000', 32: 'film', 33: 'jakarta', 34: 'amerika', 35: 'korban', 36: '19', 37: '1', 38: 'keluarga', 39: 'juta', 40: 'tim', 41: 'lain', 42: 'perusahaan', 43: 'katanya', 44: 'hukum', 45: 'anggota', 46: 'menteri', 47: 'hidup', 48: 'kesehatan', 49: 'media', 50: 'kami', 51: 'serangan', 52: 'wilayah', 53: '10', 54: 'politik', 55: 'sosial', 56: 'partai', 57: 'masuk', 58: 'the', 59: 'daerah', 60: 'air', 61: 'cina', 62: 'covid', 63: 'virus', 64: 'jalan', 65: 'benar', 66: 'negeri', 67: 'kerja', 68: 'pesawat', 69: 'foto', 70: 'sekolah', 71: 'selatan', 72: 'utara', 73: 'laki', 74: 'barat', 75: 'm

In [ ]:
# Predict Manual
%xmode Verbose
x = x.reshape(1,-1)

## encode X
encoder_out, state_h, state_c = encoder_model.predict(x)
## prepare loop
## sum_input = np.zeros(shape=(300, 0, 0, 0))
y_inp = np.array([tokenizer.word_index[special_tokens[0]]])
y_expand=np.expand_dims(y_inp,axis=1)
predicted_text = ""
stop = False
while not stop:
    ## predict dictionary probability distribution
    probs, new_state_h, new_state_c = decoder_model.predict(
                      [y_expand, encoder_out, state_h, state_c])
    
    ## get predicted word
    voc_idx = np.argmax(probs[0,-1,:],axis=0)
    if voc_idx == 0:
      break
    print(voc_idx)
    pred_word = tokenizer.index_word[voc_idx]
    
    ## check stop
    if (pred_word != special_tokens[1]) and (len(predicted_text.split()) < y_test.shape[1]):
      predicted_text = predicted_text +" "+ pred_word
      # print(predicted_text)
    else:
      stop = True
    
    ## next
    y_inp = np.array([voc_idx])
    y_expand=np.expand_dims(y_inp,axis=1)
    state_h, state_c = new_state_h, new_state_c

Exception reporting mode: Verbose
1
1
1176
462
158
9


In [ ]:
print(predicted_text)

 orang orang yahudi ditangkap suriah


## Saved Model and Send to Cloud Bucket

In [ ]:
import pickle

with open('encoder_model.pkl', 'wb') as files:
    pickle.dump(encoder_model, files)

INFO:tensorflow:Assets written to: ram://8f5478d2-2a03-43e2-9470-bbe3c93cc5a7/assets


INFO:tensorflow:Assets written to: ram://8f5478d2-2a03-43e2-9470-bbe3c93cc5a7/assets


In [ ]:
print(len(art_vocabulary))
print(len(sum_vocabulary))

53910
54448


In [ ]:
vocabulary = {}
vocabulary.update(tokenizer.index_word)

In [ ]:
a_file = open("data.json", "w")
json.dump(vocabulary, a_file)
a_file.close()

a_file = open("data.json", "r")
output = a_file.read()
print(output)
a_file.close()

{"1": "orang", "2": "itu", "3": "indonesia", "4": "negara", "5": "ini", "6": "anak", "7": "pemerintah", "8": "xstartx", "9": "xendx", "10": "rumah", "11": "kota", "12": "presiden", "13": "saya", "14": "perempuan", "15": "dunia", "16": "warga", "17": "salah", "18": "memiliki", "19": "inggris", "20": "lalu", "21": "mereka", "22": "bbc", "23": "kelompok", "24": "masyarakat", "25": "tersebut", "26": "kali", "27": "as", "28": "tahun", "29": "polisi", "30": "terkait", "31": "000", "32": "film", "33": "jakarta", "34": "amerika", "35": "korban", "36": "19", "37": "1", "38": "keluarga", "39": "juta", "40": "tim", "41": "lain", "42": "perusahaan", "43": "katanya", "44": "hukum", "45": "anggota", "46": "menteri", "47": "hidup", "48": "kesehatan", "49": "media", "50": "kami", "51": "serangan", "52": "wilayah", "53": "10", "54": "politik", "55": "sosial", "56": "partai", "57": "masuk", "58": "the", "59": "daerah", "60": "air", "61": "cina", "62": "covid", "63": "virus", "64": "jalan", "65": "benar"

In [ ]:
output[3]

'"'

In [ ]:
!mkdir -p saved_model
encoder_model.save('saved_model/my_model_encoder')
decoder_model.save('saved_model/my_model_decoder') 

INFO:tensorflow:Assets written to: saved_model/my_model_encoder/assets


INFO:tensorflow:Assets written to: saved_model/my_model_encoder/assets


INFO:tensorflow:Assets written to: saved_model/my_model_decoder/assets


INFO:tensorflow:Assets written to: saved_model/my_model_decoder/assets


In [ ]:
# my_model directory
!ls saved_model

# Contains an assets folder, saved_model.pb, and variables folder.
!ls saved_model/my_model

my_model
assets	keras_metadata.pb  saved_model.pb  variables


In [ ]:
!zip -r "/content/model.zip" "/content/saved_model"

  adding: content/saved_model/ (stored 0%)
  adding: content/saved_model/my_model_decoder/ (stored 0%)
  adding: content/saved_model/my_model_decoder/assets/ (stored 0%)
  adding: content/saved_model/my_model_decoder/keras_metadata.pb (deflated 90%)
  adding: content/saved_model/my_model_decoder/saved_model.pb (deflated 90%)
  adding: content/saved_model/my_model_decoder/variables/ (stored 0%)
  adding: content/saved_model/my_model_decoder/variables/variables.index (deflated 40%)
  adding: content/saved_model/my_model_decoder/variables/variables.data-00000-of-00001 (deflated 36%)
  adding: content/saved_model/my_model_encoder/ (stored 0%)
  adding: content/saved_model/my_model_encoder/assets/ (stored 0%)
  adding: content/saved_model/my_model_encoder/keras_metadata.pb (deflated 90%)
  adding: content/saved_model/my_model_encoder/saved_model.pb (deflated 90%)
  adding: content/saved_model/my_model_encoder/variables/ (stored 0%)
  adding: content/saved_model/my_model_encoder/variables/va

In [ ]:
# from google.colab import files
# files.download("/content/file.zip")


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
from google.colab import auth
auth.authenticate_user()


project_id = 'pukulenam-test'
!gcloud config set project {project_id}

Updated property [core/project].


In [ ]:

#Define bucket name
bucket_name = 'pukulenam-test-deploy'


# Copy the file to our new bucket.
# Change /tmp/to_upload.txt DIR TO YOUR DESIRED FILE DIRECTORY
!gsutil cp /content/model.zip gs://{bucket_name}/
  

Copying file:///content/model.zip [Content-Type=application/zip]...
==> NOTE: You are uploading one or more large file(s), which would run
significantly faster if you enable parallel composite uploads. This
feature can be enabled by editing the
"parallel_composite_upload_threshold" value in your .boto
configuration file. However, note that if you do this large files will
be uploaded as `composite objects
<https://cloud.google.com/storage/docs/composite-objects>`_,which
means that any user who downloads such objects will need to have a
compiled crcmod installed (see "gsutil help crcmod"). This is because
without a compiled crcmod, computing checksums on composite objects is
so slow that gsutil disables downloads of composite objects.

|
Operation completed over 1 objects/346.2 MiB.                                    


In [ ]:

#Define bucket name
bucket_name = 'pukulenam-test-deploy'


# Copy the file to our new bucket.
# Change /tmp/to_upload.txt DIR TO YOUR DESIRED FILE DIRECTORY
!gsutil cp /content/data.json gs://{bucket_name}/
  

Copying file:///content/data.json [Content-Type=application/json]...
\
Operation completed over 1 objects/2.4 MiB.                                      
